# QA Legal Refugees Project

## Environment


! pip install -U "transformers==4.38.0" --upgrade
! pip install git+https://github.com/huggingface/trl
! pip install peft
! pip install accelerate
! pip intall datasets
! pip install bitsandbytes

## Base Model

We used Gemma 7b as base model for 3 reason
- Tokenizer size with multiple [languages](https://www.shelpuk.com/post/llm-practitioner-s-guide-gemma-a-game-changing-multilingual-llm)
- is SOTA for its size 
- A lot of material available to consult

## Dataset preparation

We wanted to make a conversation model so we investigated the base model prompt in order to make conversational base on [chatml format](https://github.com/MicrosoftDocs/azure-docs/blob/main/articles/ai-services/openai/includes/chat-markup-language.md#working-with-chat-markup-language-chatml)

we identified the special tokens so the model could understand the different roles in the conversation

Example 
```
<bos><|im_start|>system
You are Gemma.<|im_end|>
<|im_start|>user
Hello, how are you?<|im_end|>
<|im_start|>assistant
I'm doing great. How can I help you today?<|im_end|>\n<eos>
```

so we used [Phil Schmid's gemma chatml tokenizer](https://huggingface.co/philschmid/gemma-tokenizer-chatml) to adapt our dataset for training

In [ ]:
## load dataset
from datasets import load_dataset

dataset = load_dataset("somosnlp/instruct-legal-refugiados-es")

In [ ]:
# load tokenizer 
tokenizer_id = "philschmid/gemma-tokenizer-chatml"
tokenizer = AutoTokenizer.from_pretrained(tokenizer_id)
tokenizer.padding_side = 'right' # to prevent warnings

In [ ]:
## Map functions
def create_message_column(row):
    messages = []
    user = {
        "content": f"{row['instruction']}/n{row['input']}",
        "role": "user"
    }
    messages.append(user)
    assistant = {
        "content": f"{row['output']}",
        "role": "assistant"
    }
    messages.append(assistant)
    return {"messages": messages}

def format_dataset_chatml(row):
    return {"text": tokenizer.apply_chat_template(row["messages"], add_generation_prompt=False, tokenize=False)}

In [ ]:
## prepare the dataset
dataset = dataset.map(create_message_column)
dataset = dataset.map(format_dataset_chatml)

## Train Model

To finetune Gemma we used PEFT, Lora and SFTTtrainer. The model was trained in a RTX 4090 from Vast.ai founded by the author

In [ ]:
import torch
from transformers import AutoModelForCausalLM, BitsAndBytesConfig

# cache_dir was set because the rent machine didn't have space in default directory
# Hugging Face model id
model_id = "google/gemma-7b"

# BitsAndBytesConfig int-4 config
bnb_config = BitsAndBytesConfig(
    load_in_4bit=True, bnb_4bit_use_double_quant=True, bnb_4bit_quant_type="nf4", bnb_4bit_compute_dtype=torch.bfloat16
)

# Load model and tokenizer
model = AutoModelForCausalLM.from_pretrained(
    model_id,
    device_map="auto",
    attn_implementation="flash_attention_2",
    torch_dtype=torch.bfloat16,
    quantization_config=bnb_config,
    cache_dir="/sys/fs/cgroup/models"
)

In [ ]:
from peft import LoraConfig

peft_config = LoraConfig(
    lora_alpha=8,
    lora_dropout=0.05,
    r=6,
    bias="none",
    target_modules="all-linear",
    task_type="CAUSAL_LM"
)

In [ ]:
from transformers import TrainingArguments

args = TrainingArguments(
    output_dir="/sys/fs/cgroup/models/model/location",
    num_train_epochs=3,
    per_device_train_batch_size=2,
    gradient_accumulation_steps=2,
    gradient_checkpointing=True,
    optim="adamw_torch_fused",
    logging_steps=10,
    save_strategy="epoch",
    bf16=True,
    tf32=True,
    max_grad_norm=0.3,                      # max gradient norm based on QLoRA paper
    warmup_ratio=0.03,                      # warmup ratio based on QLoRA paper
    lr_scheduler_type="constant",           # use constant learning rate scheduler
    push_to_hub=True,
    hub_private_repo=True,
    hub_model_id="model_name",                      # push model to hub
    report_to="wandb",
    seed=66,
)

In [ ]:
from trl import SFTTrainer

max_seq_length =1512

trainer = SFTTrainer(
    model=model,
    args=args,
    train_dataset=dataset,
    dataset_text_field="text",
    peft_config=peft_config,
    max_seq_length=max_seq_length,
    tokenizer=tokenizer,
    packing=True,
    dataset_kwargs={
        "add_special_tokens": False, # We template with special tokens
        "append_concat_token": False, # No need to add additional separator token
    }
)

In [ ]:
trainer.train()

In [ ]:
trainer.push_to_hub()

## Merge adapter into original model
When using QLoRA, we only train adapters and not the full model. This means when saving the model during training we only save the adapter weights and not the full model. You can merge the adapter weights into the model weights using the `merge_and_unload` method and then save the model with the `save_pretrained` method.

In [ ]:
from peft import PeftModel, PeftConfig
from transformers import AutoModelForCausalLM

peft_model_id = "model_name"
base_model_id = "google/gemma-7b-it"
config = PeftConfig.from_pretrained(peft_model_id, cache_dir="/sys/fs/cgroup/models")
model = AutoModelForCausalLM.from_pretrained(base_model_id, cache_dir="/sys/fs/cgroup/models")
model = PeftModel.from_pretrained(model, peft_model_id ,cache_dir="/sys/fs/cgroup/models")

In [ ]:
tokenizer = AutoTokenizer.from_pretrained(peft_model_id, cache_dir="/sys/fs/cgroup/models")

In [ ]:
model = model.merge_and_unload()

In [ ]:
model.save_pretrained("/sys/fs/cgroup/model/location", push_to_hub=True, private=True)
tokenizer.save_pretrained("/sys/fs/cgroup/model/location", push_to_hub=True, private=True)